In [28]:
%cd /Users/kyle/Dropbox/PFH/iPFH/idxPARAM
msm=pd.read_csv('msm_rho_df.csv')

/Users/kyle/Dropbox/PFH/iPFH/idxPARAM


In [51]:
%cd ~/Dropbox/PFH/iPFH/IdxSL/

wf=pd.read_csv("ffa_win_slope_long.csv")
wh=pd.read_csv("ppa_win_neg_slope_long.csv")
wh['av_slope']=np.abs(wh.slope)

/Users/kyle/Dropbox/PFH/iPFH/IdxSL


In [29]:
from scipy.stats import pearsonr, spearmanr
spearmanr(msm.vFF, z)

(-0.10877192982456141, 0.6575797528910039)

In [52]:
wf['combined_slope'] = wf.slope+wh.av_slope

In [2]:
%cd ~/Dropbox/PFH/iPFH/IdxTC/

wtcf=pd.read_csv("WIN_AllSx_FaceClusters.csv", index_col=0)
wtch=pd.read_csv("WIN_AllSx_HouseClusters.csv", index_col=0)
stcf=pd.read_csv("WSS_AllSx_FaceClusters.csv", index_col=0)
stch=pd.read_csv("WSS_AllSx_HouseClusters.csv", index_col=0)

/Users/kyle/Dropbox/PFH/iPFH/IdxTC


In [11]:
for df in [wf, wh, sf, sh]:
      if 'sx' in df.columns:
            sx=df['sx']
            df['sx']=[int(idx[1:]) for idx in sx]
            
            

In [13]:
#sh = sh[~sh.cond.isin(['hc', 'nc', 'fc'])]
#sf = sf[~sf.cond.isin(['hc', 'nc', 'fc'])]

wh = wtch[~wtch.cond.isin(['hc', 'nc', 'fc', 'ncface', 'nchouse'])]
wf = wtcf[~wtcf.cond.isin(['hc', 'nc', 'fc', 'ncface', 'nchouse'])]

In [24]:
sfmu = sf.groupby('cond').mean()
shmu = sh.groupby('cond').mean()
cond = sfmu.index.tolist()


In [25]:
for c in cond:
      plt.plot(sfmu.loc[c, '1':])
      plt.plot(shmu.loc[c, '1':])

In [23]:
def get_slopes(df, start='2', direction='pos'):

      slopes=[]

      if 'idx' in df.columns:
            sub_id_string = 'idx'
      elif 'sx' in df.columns:
            sub_id_string = 'sx'

      for i, (sx, sxvec) in enumerate(df.groupby(sub_id_string)):
            
            xhigh=np.where(sxvec.values==sxvec[start].values)[1][0]
            yhigh=sxvec[start].values[0]

            if direction=='pos':
                  xlow=np.where(sxvec.values==sxvec[start].values)[1][0]
                  ylow=sxvec[start].values[0]
                  xhigh=np.where(sxvec.values==np.max(sxvec.ix[:,start:].values[0][1:]))[1][0]
                  yhigh=np.max(sxvec.ix[:,start:].values)

            elif direction=='neg':
                  xlow=np.where(sxvec.values==np.min(sxvec.ix[:,start:].values[0][1:]))[1][0]
                  ylow=np.min(sxvec.ix[:,start:].values)
                  xhigh=np.where(sxvec.values==sxvec[start].values)[1][0]
                  yhigh=sxvec[start].values[0]
            else: 
                  print "direction must be string, 'pos' or 'neg'"
                  return []

            slopes.append((yhigh-ylow)/(xhigh-xlow))
      return np.array(slopes)    




In [21]:
for idx, idxdf in wf.groupby('sx'):
      f, ax = plt.subplots(1)
      
      for c in idxdf.cond.unique():
            if 'house' in c:
                  color='r'
                  if c[0]=='h':
                        a=1
                  else:
                        a=.5
            elif 'face' in c:
                  color='b'
                  if c[0]=='f':
                        a=1
                  else:
                        a=.5
            ax.plot(idxdf.ix[idxdf.cond==c].loc[:, '1':].values[0], label=c, color=color, alpha=a)
      
      ax.legend()
      #os.mkdir(str(idx))
      f.savefig(''.join([str(idx)+'/', 'face_tc.png']))
      

In [18]:
for idx, idxdf in wh.groupby('sx'):
      f, ax = plt.subplots(1)
      for c in idxdf.cond.unique():
            if 'house' in c:
                  color='r'
                  if c[0]=='h':
                        a=1
                  else:
                        a=.5
            elif 'face' in c:
                  color='b'
                  if c[0]=='f':
                        a=1
                  else:
                        a=.5
                        
            ax.plot(idxdf.ix[idxdf.cond==c].loc[:, '1':].values[0], label=c, color=color, alpha=a)
      
      ax.legend()
      f.savefig(''.join([str(idx)+'/', 'house_tc.png']))                    
            

In [35]:
wfslopes = wtcf.groupby('cond').apply(get_slopes, start='2')
whslopes = wtch.groupby('cond').apply(get_slopes, start='2', direction='neg')


In [36]:
x=pd.DataFrame(wfslopes.to_dict())
y=pd.DataFrame(whslopes.to_dict())
yabs=np.abs(y)
z=x.fcface - y.fcface
z2=x.hcface - y.hcface

In [26]:
y.mean().plot()

In [37]:
pearsonr(msm.vFF_n_zF2a, z)

(-0.33278971861488926, 0.16386846575899225)

In [38]:
pearsonr(msm.vHF_n_zH2a, z2)

(-0.40686437571782186, 0.083846689796754262)

In [36]:
wf

cond  sx       1       2       3       4       5       6       7  \
0         hc   8 -0.0361  0.1154  0.2289  0.2540  0.1891  0.1513  0.0810   
1         nc   8 -0.0549  0.1127  0.2668  0.0909  0.1291  0.0311 -0.0219   
2         fc   8  0.0470  0.1223  0.1725  0.2664  0.2583  0.1301  0.0942   
3     hcface   8 -0.0909 -0.1263  0.1341  0.3539  0.2648  0.2562  0.0401   
4     ncface   8 -0.0421  0.1199  0.2591  0.5399  0.4565  0.4362  0.1739   
5     fcface   8  0.0377 -0.0191  0.1273  0.3666  0.2871  0.2451  0.0050   
6    hchouse   8 -0.0167 -0.0193  0.0223  0.0045  0.0424  0.0367  0.0620   
7    nchouse   8 -0.0012  0.1424  0.0641  0.1717  0.1687  0.1820  0.1382   
8    fchouse   8 -0.0194  0.0105 -0.0704  0.0379  0.0888  0.0374 -0.0684   
9         hc  10 -0.0891  0.1456  0.2935  0.5832  0.5200  0.5073  0.1631   
10        nc  10 -0.0554  0.1532  0.4084  0.4737  0.4752  0.3771  0.3288   
11        fc  10  0.2582  0.3173  0.5496  0.6507  0.7173  0.4963  0.3014   
12    hcface  10 -0.2470 -0.4631 -0.1924  0.2393  0.9872  1.5460  0.7045   
13    ncface  10  0.0590  0.2461  0.0490  0.3458  0.6260  0.9781  0.6296   
14    fcface  10 -0.0742 -0.0369 -0.1312  0.1379  0.5262  0.7074  0.9146   
..       ...  ..     ...     ...     ...     ...     ...     ...     ...   
156   hcface  30 -0.1314 -0.2136  0.0439  0.1987  0.4805  0.3443  0.2616   
157   ncface  30 -0.0077 -0.0149  0.0757  0.2350  0.5604  0.4595  0.3283   
158   fcface  30  0.0071  0.0852  0.0192  0.1389  0.3717  0.3660  0.1486   
159  hchouse  30 -0.0488 -0.0998  0.0624  0.0747  0.0966 -0.0794 -0.0506   
160  nchouse  30 -0.0145 -0.0394  0.0767 -0.0030  0.0481 -0.0756 -0.0495   
161  fchouse  30  0.0081  0.0504 -0.0428 -0.1406 -0.0090 -0.1332 -0.0880   
162       hc  31 -0.0438 -0.1177 -0.0649 -0.0501 -0.1108  0.0327 -0.0280   
163       nc  31 -0.1043 -0.0621 -0.2071 -0.1848 -0.2171 -0.1070 -0.0491   
164       fc  31  0.0089 -0.0003 -0.1717 -0.1135 -0.0793 -0.1078  0.0140   
165   hcface  31  0.0222 -0.1263  0.2242  0.1975  0.0585 -0.1219 -0.2017   
166   ncface  31 -0.0610 -0.0984  0.1293  0.0675 -0.0161 -0.0943 -0.0393   
167   fcface  31  0.0532 -0.0087  0.0268  0.1969 -0.0271 -0.1670 -0.0822   
168  hchouse  31 -0.0041 -0.0671 -0.0398 -0.2616 -0.2787 -0.2436 -0.1836   
169  nchouse  31  0.0970  0.1360  0.1681 -0.0085 -0.1310 -0.3128 -0.0714   
170  fchouse  31  0.0966 -0.1576 -0.0147  0.0795 -0.4159 -0.1507 -0.2736   

          8       9      10      11      12  
0    0.0552  0.0507 -0.0348 -0.0430  0.0894  
1   -0.1114 -0.0386 -0.0757 -0.0023 -0.0822  
2    0.0366  0.0966  0.0450  0.0199 -0.0102  
3    0.1121  0.0324 -0.0526 -0.0762  0.0559  
4    0.0754 -0.0542  0.0154 -0.0431 -0.0313  
5   -0.0001 -0.0419 -0.0112 -0.0427 -0.0584  
6    0.1057  0.0482 -0.0459  0.0579  0.0485  
7    0.0903  0.0381  0.1227  0.0168  0.0596  
8   -0.0424  0.0286 -0.0219 -0.0036  0.0043  
9    0.0072  0.1804 -0.1745  0.0640 -0.1540  
10   0.0425 -0.0324 -0.0353  0.1248 -0.1586  
11   0.0650 -0.3207 -0.0492 -0.0649 -0.2785  
12   0.6693 -0.1785  0.0686 -0.2695 -0.0735  
13   0.4346 -0.1926 -0.2189 -0.6153 -0.5010  
14   0.2766 -0.0179 -0.0717 -0.2870 -0.0846  
..      ...     ...     ...     ...     ...  
156  0.0385 -0.1887 -0.2149  0.0092 -0.0596  
157 -0.0708 -0.1118 -0.1419  0.0245  0.0423  
158 -0.0138 -0.1647 -0.1274 -0.0122  0.1016  
159 -0.0445 -0.1157 -0.1410 -0.0029  0.0522  
160 -0.1686 -0.0900 -0.1339 -0.0193  0.0521  
161 -0.0787 -0.1613 -0.1788 -0.0329  0.0395  
162  0.0172 -0.0292 -0.0705 -0.0272 -0.0776  
163  0.0054 -0.1348 -0.0558 -0.1083 -0.1149  
164  0.0085 -0.0320  0.0673  0.0780  0.0839  
165 -0.2204 -0.2789 -0.0099  0.0086  0.0810  
166 -0.1725 -0.1029  0.0068 -0.0810 -0.0526  
167 -0.2120 -0.2259 -0.1716 -0.0382 -0.0152  
168 -0.2578 -0.1116 -0.0652 -0.0579  0.0026  
169 -0.0768  0.0035  0.1245  0.0250  0.0450  
170 -0.2176 -0.0400 -0.1327  0.0789  0.2095  

[171 rows x 14 columns]